<a href="https://colab.research.google.com/github/hmanoj26/7316/blob/main/7316_setup_2026.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [8]:
!pip install geemap
!pip install ipywidgets
!pip install whiteboxgui

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 108.6/108.6 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.0/74.0 kB 5.5 MB/s eta 0:00:00


In [12]:
# !pip install geemap
# !pip install ipywidgets

import os
import ee
import geemap
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import json
import whiteboxgui


import ipywidgets as widgets
from IPython.display import display

# # Trigger the authentication flow.
# ee.Authenticate()

# # Initialize the library.
# ee.Initialize(project='remote-sensing-486415')

Decompressing WhiteboxTools_linux_musl.zip ...
WhiteboxTools package directory: /usr/local/lib/python3.12/dist-packages/whitebox


In [13]:
# Trigger the authentication flow.
ee.Authenticate()

# Initialize the library.
ee.Initialize(project='remote-sensing-486415')

In [21]:
map = geemap.Map()
map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

First, let's create a Python file named `my_functions.py` that contains a simple reusable function. We'll use the `%%writefile` magic command to save the content directly into a file in the Colab environment.

In [22]:
dem = ee.Image('USGS/SRTMGL1_003')
vis_params = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']
}
map.addLayer(dem, vis_params, 'SRTM DEM', True, 0.5)

## Selecting Landsat Images

**Surface Reflectance** [Landsat Data](https://developers.google.com/earth-engine/datasets/catalog/landsat)

Landsat 9: LANDSAT/LC09/C01/T1_SR

Landsat 8: LANDSAT/LC08/C01/T1_SR

Landsat 7: LANDSAT/LE07/C01/T1_SR

Landsat 5: LANDSAT/LT05/C01/T1_SR


In [34]:
def get_map_feature():
  drawn_features = map.draw_features
  if drawn_features:
      print(f"Found {len(drawn_features)} drawn features.")
      for i, feature in enumerate(drawn_features):
          # print(f"\nFeature {i+1}:")
          # Access the geometry of the drawn feature using .geometry()
          # geometry = feature.geometry()
          # print(json.dumps(geometry.getInfo(), indent=2))

          # You can convert this to an ee.Geometry object if needed
          return ee.Geometry(feature.geometry())
  else:
      print("No features have been drawn on the map yet. Please use the drawing tools on the map to draw a polygon or other shape.")

In [35]:
search_bounds = get_map_feature()

Found 1 drawn features.


First, let's define a list of common Earth Engine Landsat datasets to choose from. Then, we'll create a dropdown to select one.

In [36]:
# Define available Earth Engine datasets
# Key: Display Name, Value: Earth Engine Asset ID
datasets = {
    'Landsat 9 Surface Reflectance': 'LANDSAT/LC09/C02/T1_L2',
    'Landsat 8 Surface Reflectance': 'LANDSAT/LC08/C02/T1_L2',
    'Landsat 7 Surface Reflectance': 'LANDSAT/LE07/C02/T1_L2',
    'Landsat 5 Surface Reflectance': 'LANDSAT/LT05/C02/T1_L2'
}

# Global variable to store the selected collection
global collection
collection = None # Initialize to None until a selection is made

# Create a Dropdown widget for datasets
dataset_dropdown = widgets.Dropdown(
    options=list(datasets.keys()),
    description='Select Dataset:',
    disabled=False,
    layout={'width': 'max-content'}
)

# Output widget to display selected dataset information
dataset_output = widgets.Output()

def on_dataset_select(change):
    global collection
    with dataset_output:
        dataset_output.clear_output()
        selected_dataset_name = change['new'] # Corrected: access 'new' key using dictionary syntax
        selected_asset_id = datasets[selected_dataset_name]
        print(f"Selected Dataset: {selected_dataset_name} ({selected_asset_id})")

        # Initialize the Earth Engine ImageCollection
        collection = ee.ImageCollection(selected_asset_id)

        # After selecting a dataset, trigger the consolidated update function
        # This will re-filter and update the image dropdown based on all current criteria.
        # Check if date pickers and cloud cover slider are defined to ensure dependencies are met.
        if 'start_date_picker' in globals() and 'end_date_picker' in globals() and \
           'cloud_cover_slider' in globals() and 'search_bounds' in globals() and search_bounds is not None:
            update_image_list_dropdown() # Call the consolidated update function
        else:
            print("Warning: Some filtering widgets (date pickers, cloud cover slider) or search bounds are not yet initialized.")

# Link the dataset dropdown to the change function
dataset_dropdown.observe(on_dataset_select, names='value')

# Display the dataset dropdown
display(dataset_dropdown, dataset_output)

# Automatically select the first dataset to initialize the collection
# and trigger the first filtering for the date pickers and image dropdown.
dataset_dropdown.value = list(datasets.keys())[0]

Dropdown(description='Select Dataset:', layout=Layout(width='max-content'), options=('Landsat 9 Surface Reflec…

Output()

In [37]:
import datetime

# Global placeholder for image_dropdown to prevent NameError
# It will be properly initialized by cell b5503eae later
if 'image_dropdown' not in globals():
    image_dropdown = widgets.Dropdown(options=[], description='Placeholder Image:')

# Global placeholder for on_image_select to prevent NameError
# It will be properly initialized by cell b5503eae later
if 'on_image_select' not in globals():
    def on_image_select(change):
        # This is a placeholder. The actual function in b5503eae will override this.
        # This specific placeholder prints a warning, which is what you're seeing.
        # We'll rely on b5503eae to properly trigger the display.
        print("Warning: on_image_select not yet fully initialized. Please run cell defining image_dropdown.")

# Initial date values (can be updated by the widgets)
initial_start_date_str = '2020-01-01'
initial_end_date_str = '2020-12-31'

# Create DatePicker widgets
start_date_picker = widgets.DatePicker(
    description='Start Date',
    disabled=False,
    value=datetime.datetime.strptime(initial_start_date_str, '%Y-%m-%d').date()
)

end_date_picker = widgets.DatePicker(
    description='End Date',
    disabled=False,
    value=datetime.datetime.strptime(initial_end_date_str, '%Y-%m-%d').date()
)

# Output widget to display selected dates
date_output = widgets.Output()

# Consolidated function to update the image list and dropdown based on all filters
def update_image_list_dropdown():
    global potential_images, selected_image # Declare global for potential_images and selected_image
    # Only proceed if all necessary global variables are initialized
    if 'collection' in globals() and collection is not None and \
       'search_bounds' in globals() and search_bounds is not None and \
       'start_date' in globals() and 'end_date' in globals() and \
       'cloud_cover_percentage' in globals() and 'image_dropdown' in globals():

        potential_images = collection.filterBounds(search_bounds)
        potential_images = potential_images.filterDate(start_date, end_date)
        potential_images = potential_images.filter(ee.Filter.lt('CLOUD_COVER', cloud_cover_percentage))

        image_ids = potential_images.aggregate_array('system:index').getInfo()
        if not image_ids:
            print('No images found for the selected criteria. Please adjust your search criteria.')
            image_dropdown.options = []
            selected_image = None # No image selected if list is empty
        else:
            image_dropdown.options = image_ids
            # Setting image_dropdown.value here will trigger the on_image_select observer
            # AFTER b5503eae has properly set it up.
            # If b5503eae hasn't run yet, the placeholder on_image_select will be called.
            image_dropdown.value = image_ids[0] # Select the first image by default
            print(f'Found {len(image_ids)} images for the current criteria.')
            # We no longer manually trigger on_image_select here. We rely on the observe mechanism.
    else:
        print("Warning: Some filtering parameters are not yet defined. Cannot update image list.")
        # Ensure image_dropdown exists before trying to modify its options
        if 'image_dropdown' in globals():
            image_dropdown.options = []
        selected_image = None


def on_date_change(change):
    global start_date, end_date # Declare global to modify the variables
    with date_output:
        date_output.clear_output()
        start_date = start_date_picker.value.strftime('%Y-%m-%d')
        end_date = end_date_picker.value.strftime('%Y-%m-%d')
        print(f"Selected Date Range: {start_date} to {end_date}")
        # Now trigger the consolidated update function
        update_image_list_dropdown()

# Link date pickers to the change function
start_date_picker.observe(on_date_change, names='value')
end_date_picker.observe(on_date_change, names='value')

# Display the widgets
display(start_date_picker, end_date_picker, date_output)

# Retrieve the current values from the date pickers and assign to global variables
# This relies on the user re-running the cell after making a selection in the picker
global start_date, end_date
start_date = start_date_picker.value.strftime('%Y-%m-%d')
end_date = end_date_picker.value.strftime('%Y-%m-%d')

# Initial call to update the image list and dropdown based on initial date values.
# This call also sets the initial 'start_date' and 'end_date' globals.
on_date_change({'new': None}) # Pass a dummy change event to trigger initial filtering

DatePicker(value=datetime.date(2020, 1, 1), description='Start Date')

DatePicker(value=datetime.date(2020, 12, 31), description='End Date')

Output()

In [38]:
# Global variable for cloud cover percentage
global cloud_cover_percentage
cloud_cover_percentage = 100 # Initial value

# Create a slider widget for cloud cover percentage
cloud_cover_slider = widgets.IntSlider(
    value=cloud_cover_percentage,
    min=0,
    max=100,
    step=1,
    description='Max Cloud Cover (%):',
    disabled=False,
    continuous_update=False, # Only update when slider is released
    orientation='horizontal',
    readout=True,
    readout_format='d', # Corrected from 'd%' to 'd'
    layout={'width': '500px'}
)

# Output widget to display selected cloud cover
cloud_cover_output = widgets.Output()

def on_cloud_cover_change(change):
    global cloud_cover_percentage
    with cloud_cover_output:
        cloud_cover_output.clear_output()
        cloud_cover_percentage = change['new'] # Corrected: access 'new' key using dictionary syntax
        print(f"Selected Max Cloud Cover: {cloud_cover_percentage}%")

        # Re-filter the image collection based on the new cloud cover
        # Trigger the consolidated update function
        # Check if collection and search_bounds are defined
        if 'collection' in globals() and collection is not None and 'search_bounds' in globals() and search_bounds is not None:
            update_image_list_dropdown()
        else:
            print("Warning: Please ensure a dataset is selected and a region is drawn on the map.")

# Link the slider to the change function
cloud_cover_slider.observe(on_cloud_cover_change, names='value')

# Display the slider
display(cloud_cover_slider, cloud_cover_output)

# Initial call to set the cloud_cover_percentage global and trigger update.
on_cloud_cover_change({'new': cloud_cover_slider.value}) # Pass initial value to trigger filtering

IntSlider(value=100, continuous_update=False, description='Max Cloud Cover (%):', layout=Layout(width='500px')…

Output()

In [39]:
print(f"Image Collection: {collection}")
print(f"Start Date: {start_date}")
print(f"End Date: {end_date}")
print(f"Cloud Cover: <= {cloud_cover_percentage}%")

Image Collection: ee.ImageCollection({
  "functionInvocationValue": {
    "functionName": "ImageCollection.load",
    "arguments": {
      "id": {
        "constantValue": "LANDSAT/LC09/C02/T1_L2"
      }
    }
  }
})
Start Date: 2020-01-01
End Date: 2025-12-31
Cloud Cover: <= 15%


In [40]:
potential_images = collection.filterBounds(search_bounds)
potential_images = potential_images.filterDate(start_date, end_date)
potential_images = potential_images.filter(ee.Filter.lt('CLOUD_COVER', cloud_cover_percentage))
print(f"Initial potential_images collection created with {potential_images.size().getInfo()} images.")

Initial potential_images collection created with 83 images.


In [41]:
# Define potential_images based on current selections
# Ensure collection and search_bounds are defined before attempting to filter.
if 'collection' in globals() and collection is not None and \
   'search_bounds' in globals() and search_bounds is not None and \
   'start_date' in globals() and 'end_date' in globals() and \
   'cloud_cover_percentage' in globals():

    potential_images = collection.filterBounds(search_bounds)
    potential_images = potential_images.filterDate(start_date, end_date)
    potential_images = potential_images.filter(ee.Filter.lt('CLOUD_COVER', cloud_cover_percentage))
    print(f"Initial potential_images collection created with {potential_images.size().getInfo()} images.")
else:
    print("Warning: Some filtering parameters (collection, search_bounds, dates, or cloud cover) are not yet defined.")
    print("Please ensure you've run the cells for dataset selection, drawing a region, date pickers, and the cloud cover slider.")
    potential_images = None # Assign None or an empty collection if not all parameters are ready

potential_images

Initial potential_images collection created with 83 images.


### Get Image Metadata

To create a dropdown, we first need a list of identifiers for each image in the `potential_images` collection. We'll extract the `system:index` property, which usually serves as a unique ID for each image.

In [42]:
image_ids = potential_images.aggregate_array('system:index').getInfo()

if not image_ids:
    print('No images found in the collection. Please adjust your search criteria.')
else:
    print(f'Found {len(image_ids)} images. Here are the first 5 IDs:')
    for i, image_id in enumerate(image_ids[:5]):
        print(f'{i+1}. {image_id}')

Found 83 images. Here are the first 5 IDs:
1. LC09_033033_20211107
2. LC09_033033_20211112
3. LC09_033033_20211213
4. LC09_033033_20220130
5. LC09_033033_20220303


Now, let's create the dropdown widget using these image IDs. We'll also define a function that gets executed whenever a new image is selected from the dropdown, which will then add the selected image to the map.

In [43]:
image_dropdown = widgets.Dropdown(
    options=[], # Initialize with an empty list of options to prevent NameError
    description='Select Image:',
    disabled=False,
    layout={'width': 'max-content'}
)

def on_image_select(change):
    global selected_image # Declare selected_image as global
    selected_image_id = change.new
    if selected_image_id:
        selected_image = potential_images.filter(ee.Filter.eq('system:index', selected_image_id)).first()

        # Define the region for statistics. Use search_bounds if available, otherwise the image's own footprint.
        region_for_stats = search_bounds if search_bounds else selected_image.geometry()

        # Calculate mean and standard deviation for dynamic stretching
        # Use a dictionary to store results for multiple reducers
        stats = selected_image.select(['SR_B4', 'SR_B3', 'SR_B2']).reduceRegion(
            reducer=ee.Reducer.mean().combine(ee.Reducer.stdDev(), None, True),
            geometry=region_for_stats,
            scale=30,
            maxPixels=1e9
        ).getInfo()

        # Define the number of standard deviations for the stretch
        std_dev_multiplier = 2

        # Extract mean and stdDev values for each band and create dynamic visualization parameters
        dynamic_rgb_vis_params = {
            'bands': ['SR_B4', 'SR_B3', 'SR_B2'],
            'min': [
                stats['SR_B4_mean'] - std_dev_multiplier * stats['SR_B4_stdDev'],
                stats['SR_B3_mean'] - std_dev_multiplier * stats['SR_B3_stdDev'],
                stats['SR_B2_mean'] - std_dev_multiplier * stats['SR_B2_stdDev']
            ],
            'max': [
                stats['SR_B4_mean'] + std_dev_multiplier * stats['SR_B4_stdDev'],
                stats['SR_B3_mean'] + std_dev_multiplier * stats['SR_B3_stdDev'],
                stats['SR_B2_mean'] + std_dev_multiplier * stats['SR_B2_stdDev']
            ]
        }

        # It's good practice to clear previous layers to avoid clutter
        current_layers = list(map.layers)
        for layer in current_layers:
            if f'Selected Image: {selected_image_id}' in layer.name or 'Landsat Image' in layer.name:
                map.remove_layer(layer)

        map.addLayer(selected_image, dynamic_rgb_vis_params, f'Selected Image: {selected_image_id}')
        map.centerObject(selected_image, 10)
    else:
        print("No image selected.")

image_dropdown.observe(on_image_select, names='value')

# Display the dropdown
display(image_dropdown)

# Initialize selected_image as None or the first image to make it globally available
# It will be updated by the dropdown selection.
selected_image = None # Or initialize with potential_images.first() if a default image is always selected

# The initial population of options and selection logic is now handled by update_image_list_dropdown
# which is called by the dataset, date, and cloud cover change events.
# No need for an 'if image_ids:' block here as options are set by update_image_list_dropdown.

# Explicitly call update_image_list_dropdown to populate the image_dropdown on initial run of this cell
update_image_list_dropdown()

Dropdown(description='Select Image:', layout=Layout(width='max-content'), options=(), value=None)

Found 83 images for the current criteria.


In [45]:
if selected_image:
    print("Globally accessible selected image:")
    print(f"Image ID: {selected_image.get('system:index').getInfo()}")
    print(f"Image bands: {selected_image.bandNames().getInfo()}")
else:
    print("No image has been selected yet from the dropdown. Please select an image.")

Globally accessible selected image:
Image ID: LC09_034033_20250113
Image bands: ['SR_B1', 'SR_B2', 'SR_B3', 'SR_B4', 'SR_B5', 'SR_B6', 'SR_B7', 'SR_QA_AEROSOL', 'ST_B10', 'ST_ATRAN', 'ST_CDIST', 'ST_DRAD', 'ST_EMIS', 'ST_EMSD', 'ST_QA', 'ST_TRAD', 'ST_URAD', 'QA_PIXEL', 'QA_RADSAT']
